In [1]:
import pandas as pd
import matplotlib as mpl
import json
from bokeh.io import output_notebook
from bokeh.models import (
    GeoJSONDataSource,
    HoverTool,
    LinearColorMapper,
    ColumnDataSource,
    LogColorMapper,
    LogTicker,
    ColorBar
)
from bokeh.plotting import figure, show
from bokeh.layouts import row
from bokeh.palettes import Viridis6 as palette
from bokeh.palettes import RdYlGn11 as palette2

mpl.rcParams['figure.figsize'] = (16,8)
#mpl.style.use('ggplot')
palette.reverse()

In [2]:
#df = pd.read_csv("../data/crimes_with_zip_no_2017.csv")
#df = pd.read_csv("../data/crimes_with_zip.csv")
df = pd.read_csv("../data/crimes_in_polygon.csv")
df["Zip"] = df["Zip"].astype('category')

In [3]:
crimes_by_zip = df.groupby("Zip").size()
crimes_by_zip.index = crimes_by_zip.index.astype("str")
total_crimes = crimes_by_zip.sum() 
crimes_by_zip = crimes_by_zip\
                            .div(total_crimes)\
                            .multiply(100)\
                            .round(2)\
                            .to_dict()

In [4]:
output_notebook()
color_mapper = LogColorMapper(palette=palette2,
                                 low=min(crimes_by_zip.values()),
                                 high=max(crimes_by_zip.values()))

with open(r'../map/zip/zip_codes.geojson', 'r') as f:
    geojson = json.loads(f.read())
    # append aggregated crime counts
    for i in range(len(geojson["features"])):
        di = geojson["features"][i]
        di_id = di["properties"]["zip"]
        if di_id in crimes_by_zip:
            di["properties"]["crime_rate"] = crimes_by_zip[di_id]
        else:
            di["properties"]["crime_rate"] = "None"
    geojson = json.dumps(geojson)
    geo_source = GeoJSONDataSource(geojson=geojson)
    
hover = HoverTool(tooltips=[
    ("zip", "@zip"),
    ("crime_rate", "@crime_rate%")
])

psource = ColumnDataSource(df[["Latitude", "Longitude"]].sample(10000))

color_bar = ColorBar(color_mapper=color_mapper,
                     label_standoff=12, border_line_color=None, location=(0,0),
                    major_label_text_font_size='10pt')

p1 = figure(title="Chicago crimes per ZIP", 
           tools=[hover, "pan,wheel_zoom,box_zoom,reset"], 
           x_axis_location=None, 
           y_axis_location=None,
           toolbar_location=None)

p1.grid.grid_line_color = None

p1.patches('xs', 'ys', 
          line_color='black', 
          fill_color={'field': 'crime_rate', 'transform': color_mapper},
          line_width=1, 
          source=geo_source)

p1.cross('Longitude', 'Latitude', source=psource, color='blue', size=4, alpha=0.1)  

p1.add_layout(color_bar, 'right')

Loading BokehJS ...

Next lets see crime rates per zip code with 10000 randomly sampled points plotted over the zip districts

In [5]:
show(p1)

There seems to be two big hotspots for crimes. In red areas amount of crimes done is around 5% of total crimes done in Chicago.

In [6]:
school_df = pd.read_csv("../assets/schooldata.csv")\
                .groupby("ZIP Code")\
                .mean()

school_df.rename(columns={'Rate of Misconducts (per 100 students) ': 'Misconducts'}, inplace=True)

ss_series = school_df["Safety Score"]
mis_series = school_df["Misconducts"]

In [7]:
output_notebook()

color_mapper = LogColorMapper(palette=list(reversed(palette2)), low=ss_series.min(), high=ss_series.max())

with open(r'../map/zip/zip_codes.geojson', 'r') as f:
    geojson = json.loads(f.read())
    for i in range(len(geojson["features"])):
        di = geojson["features"][i]
        di_id = int(di["properties"]["zip"])
        if di_id in ss_series.keys():
            di["properties"]["safety_score"] = ss_series.get(int(di_id))
        else:
            di["properties"]["safety_score"] = "None"
    geojson = json.dumps(geojson)
    geo_source = GeoJSONDataSource(geojson=geojson)
    

hover = HoverTool(tooltips=[
    ("zip", "@zip"),
    ("safety_score", "@safety_score")
])

color_bar = ColorBar(color_mapper=color_mapper,
                     label_standoff=12, border_line_color=None, location=(0,0),
                    major_label_text_font_size='10pt')
    
p2 = figure(title="Chicago school safety score per ZIP", 
           tools=[hover, "pan,wheel_zoom,box_zoom,reset"], 
           x_axis_location=None, 
           y_axis_location=None,
           toolbar_location=None)

p2.grid.grid_line_color = None

p2.patches('xs', 'ys', 
          line_color='black', 
          fill_color={'field': 'safety_score', 'transform': color_mapper},
          line_width=1, 
          source=geo_source)

p2.add_layout(color_bar, 'right')

Loading BokehJS ...

In [8]:
show(p2)

In [9]:
output_notebook()

color_mapper = LogColorMapper(palette=palette2, low=mis_series.min(), high=mis_series.max())

with open(r'../map/zip/zip_codes.geojson', 'r') as f:
    geojson = json.loads(f.read())
    for i in range(len(geojson["features"])):
        di = geojson["features"][i]
        di_id = int(di["properties"]["zip"])
        if di_id in ss_series.keys():
            di["properties"]["mis_score"] = mis_series.get(int(di_id))
        else:
            di["properties"]["mis_score"] = "None"
    geojson = json.dumps(geojson)
    geo_source = GeoJSONDataSource(geojson=geojson)
    

hover = HoverTool(tooltips=[
    ("zip", "@zip"),
    ("mis_score", "@mis_score")
])

color_bar = ColorBar(color_mapper=color_mapper,
                     label_standoff=12, border_line_color=None, location=(0,0),
                    major_label_text_font_size='10pt')
    
p3 = figure(title="Chicago school misconducts % per ZIP", 
           tools=[hover, "pan,wheel_zoom,box_zoom,reset"], 
           x_axis_location=None, 
           y_axis_location=None,
           toolbar_location=None)

p3.grid.grid_line_color = None

p3.patches('xs', 'ys', 
          line_color='black', 
          fill_color={'field': 'mis_score', 'transform': color_mapper},
          line_width=1, 
          source=geo_source)

p3.add_layout(color_bar, 'right')

show(p3)

Loading BokehJS ...

In [13]:
output_notebook()

show(row(p1,p2, p3, responsive=True))

Loading BokehJS ...